# Woche 10 #

Diese Wochen beschäftigen wir uns mit Matrizen und Vektoren.
In diesem Notebook rechnen wir ein paar (Teil)aufgaben aus dem ÜB.

In [ ]:
'''IMPORTS'''
import os;
import sys; 

# NOTE: need this to force jupyter to reload imports:
for key in list(sys.modules.keys()):
    if key.startswith('src.'):
        del sys.modules[key];

os.chdir(os.path.dirname(_dh[0]));
sys.path.insert(0, os.getcwd());

from src.thirdparty.maths import *;
from src.thirdparty.misc import *;
from src.thirdparty.render import *;
from src.maths.diagrams import *;

np.random.seed(8007253); # zur Wiederholbarkeit

In [ ]:
'''BEISPIEL-SIGNAL'''
n = 100;
u = np.zeros((n,), dtype=complex);
u[8] = -0.7
u[58] = 1j * sqrt(2);

display_signal(u, 'Beispiel eines Vektors als Signal dargestellt');

In [ ]:
'''SEMINARAUFGABE 10.4 a)'''
n = 3;
t = linspace(0, n-1, n);
i, j = np.meshgrid(t, t);
theta = 2*pi * i * j / n;

# definiere die Matrix F_n + die Vektoren u_nk
F_n = (1/sqrt(n)) * exp(-1j * theta);
u_n = [ (1/sqrt(n)) * exp(1j * theta[:, k]) for k in range(n) ];

print(dedent(
    f'''
    Matrix:

    F_{n} = \n{np.round(F_n, 3)}
    '''
));
print('');

# NOTE: Programmiersprachen können nicht exakt berechnen.
# Darum entstehen winzige Fehler, die sich durch Runden entfernen lassen.
print('Matrix-Vektor-Produkte:');
for k in range(n):
    result = F_n @ u_n[k];
    print(dedent(
        f'''

              u_{{n {k}}} = {np.round(u_n[k], 3)}
        F_n · u_{{n {k}}} = {np.round(result, 3)}
        '''
    ));

## Seminaraufgabe 10.4 b) ##

Für $i\in\{0,1,\ldots,n-1\}$ ist die $i$-te von $\mathcal{F}_{n}\,u_{n,k}$

$$
    \begin{array}{rcl}
    (\mathcal{F}_{n}\,u_{n,k})_{i}
    &= &\displaystyle\sum_{j=0}^{n-1}
        (\mathcal{F}_{n})_{ij}\,(u_{n,k})_{j}\\
    &= &\displaystyle\sum_{j=0}^{n-1}
        \tfrac{1}{\sqrt{n}}
        \exp(-\imath\tfrac{2\pi\,ij}{n})
        \cdot
        \tfrac{1}{\sqrt{n}}
        \exp(\imath\tfrac{2\pi\,kj}{n})\\
    &= &\frac{1}{n}\displaystyle\sum_{j=0}^{n-1}
        \underbrace{
            \exp(\imath\tfrac{2\pi\,(k-i)j}{n})
        }_{= r^{j}}\\
    \end{array}
$$

wobei $r := \exp(\imath\tfrac{2\pi\,(k-i)}{n})$.
Wir haben, dass
    $r = 1$
    $\Leftrightarrow$
        $\tfrac{k-i}{n} \in \mathbb{Z}$
    $\Leftrightarrow$
        $i = k$,
da $0\leq i,k \leq n-1$.
<br>
Es gilt außerdem $r^{n} = \exp(\imath 2\pi\,(k-i)) = 1$.
<br>
Aus der o.s. Berechnung erhält man also

$$
    \begin{array}{rcl}
    (\mathcal{F}_{n}\,u_{n,k})_{i}
    &= &\tfrac{1}{n}\displaystyle\sum_{j=0}^{n-1}r^{j}\\
    &= &\tfrac{1}{n}
        \left\{
        \begin{array}{lcl}
            \displaystyle\sum_{j=0}^{n-1}1 &: &i = k\\
            \dfrac{1 - r^{n}}{1 - r} &: &\text{sonst}\\
        \end{array}
        \right.\\
    &= &\tfrac{1}{n}
        \left\{
        \begin{array}{lcl}
            n &: &i = k\\
            \dfrac{1 - 1}{1 - r} &: &\text{sonst}\\
        \end{array}
        \right.\\
    &= &\left\{
        \begin{array}{lcl}
            1 &: &i = k\\
            0 &: &\text{sonst}\\
        \end{array}
        \right.\\
    &= &\delta_{ik}.\\
    \end{array}
$$

Darum $\mathcal{F}_{n}\,u_{n,k}
    = \left(\begin{matrix}
        0\\
        0\\
        \vdots\\
        1\\
        \vdots\\
        0\\
    \end{matrix}\right)
    \begin{matrix}
        \\
        \\
        \\
        \leftarrow k\\
        \\
        \\
    \end{matrix}
    = \mathbf{e}_{k}$.


In [ ]:
'''SEMINARAUFGABE 10.4 d)'''
n = 4;
t = linspace(0, n-1, n);
i, j = np.meshgrid(t, t);
theta = 2*pi * i * j / n;

# definiere die Matrix F_n + die Vektoren u_nk
F_n = (1/sqrt(n)) * exp(-1j * theta);
u_n = [ (1/sqrt(n)) * exp(1j * theta[:, k]) for k in range(n) ];

# Eingabe des Vektors:
F_mal_u = np.asarray([100, -3, 0, -3]); # = F_n @ u

'''
NOTE: Folgende Koeffizienten wurden falsch erraten.
TODO: Wie lauten die richtigen Werte? -> Aufgabe!
'''
c = [10,10,40,50];

# Aufschreibung des Signals »bzgl. der harmonischen Basis«:
# u = c[0]u_n[0] + c[1]u_n[1] + c[2]u_n[2] + c[3]u_n[3]
u_guess = sum([ c[k] * u_n[k] for k in range(n) ]);

# Anzeige der Lösung:
display_signal(u_guess, 'Geschätztes Signal');

# Verifikation von Lösung:
print(dedent(
    f'''
    %error := ‖u_guess –  u‖ / ‖u‖
            = ‖F_n · (u_guess – u)‖ / ‖F_n · u‖
                ... wieso?? [Stichwort: unitär]
            = ‖F_n · u_guess –  F_n · u‖ / ‖F_n · u‖
            = {linalg.norm(F_n @ u_guess - F_mal_u)/linalg.norm(F_mal_u):.2%}
    '''
));
